In [1]:
#use pol-stats environment

import pandas as pd
import numpy as np
import os
import cv2
from scipy.optimize import curve_fit
import colorcet as cc

import bokeh.io
import bokeh.plotting
import bokeh.models
import iqplot

bokeh.io.output_notebook()

Loading BokehJS ...

## General project files

In [2]:
# Connect to cytokinesis-zebrafish-collab server
general_info_csv_filepath = '/Volumes/cytokinesis-zebrafish-collab/magnetic_tweezers/2_analysis/CC_phases_tweezers_info.csv'

df_general_info = pd.read_csv(general_info_csv_filepath, delimiter=';')
df_general_info.columns

Index(['trackmate_file', 'before_file', 'm_phase_1_start (frame)',
       'm_phase_1_end (frame)', 'i_phase_1_start (frame)',
       'i_phase_1_end (frame)', 'm_phase_2_start (frame)',
       'm_phase_2_end (frame)', 'i_phase_2_start', 'i_phase_2_end',
       'first_pulse (frame)', 't_on (frame)', 't_off (frame)',
       'calibration (mV)', 'bead_type', 'tip_threshold', 'use', 'comments'],
      dtype='object')

### Let's look at the tracks obtain from the TrackMate

In [3]:
dt = 5/60 # min


idx = 4
# Define the path of your .csv file with tracks
filepath=df_general_info['trackmate_file'].values[idx]
tip_file = df_general_info['before_file'].values[idx]

result_dir = '/Volumes/cytokinesis-zebrafish-collab/magnetic_tweezers/3_plots/'
result_df = pd.DataFrame(columns=['FILENAME', 'TRACK_IDX', 'PULSE_START_TIME', 'MAGNET_STATUS', 'VISCOSITY'])

filename = os.path.basename(filepath).split('.')[0]  # This gets filename without extention

df = pd.read_csv(filepath, skiprows=[1, 2, 3]) # skiprows to get rid of the extensive header
df = df.sort_values(by='FRAME')

first_pulse, t_on, t_off = df_general_info.loc[df_general_info['trackmate_file']==filepath, ['first_pulse (frame)', 't_on (frame)',	't_off (frame)']].values[0]

df.head(10)     #check out your df

LABEL       ID  TRACK_ID   QUALITY  POSITION_X  POSITION_Y  \
955  ID1004879  1004879         6  1.260095  454.989749  310.672957   
318  ID1004883  1004883         2  1.355185  396.298637  331.199508   
571  ID1004881  1004881         4  1.854667  414.375458  323.841809   
174  ID1004884  1004884         1  0.948853  441.221933  339.588423   
704  ID1004880  1004880         5  1.158269  424.353404  318.606559   
445  ID1004882  1004882         3  1.048541  433.431981  330.892337   
181  ID1004905  1004905         1  0.904736  441.832713  339.015384   
982  ID1004900  1004900         6  1.250873  455.577087  310.270421   
576  ID1004902  1004902         4  1.793328  414.201620  323.935523   
449  ID1004903  1004903         3  1.165154  433.346558  329.667557   

     POSITION_Z  POSITION_T  FRAME  RADIUS  VISIBILITY  MANUAL_SPOT_COLOR  \
955         0.0         0.0      0     6.0           1                NaN   
318         0.0         0.0      0     6.0           1                NaN   
571         0.0         0.0      0     6.0           1                NaN   
174         0.0         0.0      0     6.0           1                NaN   
704         0.0         0.0      0     6.0           1                NaN   
445         0.0         0.0      0     6.0           1                NaN   
181         0.0         5.0      1     6.0           1                NaN   
982         0.0         5.0      1     6.0           1                NaN   
576         0.0         5.0      1     6.0           1                NaN   
449         0.0         5.0      1     6.0           1                NaN   

     MEAN_INTENSITY_CH1  MEDIAN_INTENSITY_CH1  MIN_INTENSITY_CH1  \
955          434.841155                 432.0              391.0   
318          439.768953                 439.0              394.0   
571          436.570397                 419.0              393.0   
174          430.534296                 428.0              388.0   
704          429.812274                 420.0              390.0   
445          434.465704                 430.0              403.0   
181          427.859206                 425.0              402.0   
982          432.559567                 427.0              397.0   
576          433.649819                 417.0              392.0   
449          435.805054                 433.0              399.0   

     MAX_INTENSITY_CH1  TOTAL_INTENSITY_CH1  STD_INTENSITY_CH1  CONTRAST_CH1  \
955              499.0             120451.0          19.168306      0.021347   
318              493.0             121816.0          17.921448      0.028751   
571              605.0             120930.0          43.179851      0.023556   
174              482.0             119258.0          14.740377      0.012063   
704              597.0             119058.0          35.077979      0.009737   
445              510.0             120347.0          19.372860      0.015035   
181              481.0             118517.0          15.214827      0.012957   
982              511.0             119819.0          20.347014      0.020812   
576              602.0             120121.0          41.627273      0.023574   
449              524.0             120718.0          20.665335      0.021302   

      SNR_CH1  
955  0.948305  
318  1.371607  
571  0.465366  
174  0.696288  
704  0.236312  
445  0.664369  
181  0.719394  
982  0.866868  
576  0.479857  
449  0.879710

### Where is the tip?

In [4]:
img = cv2.imread(tip_file, cv2.IMREAD_UNCHANGED)

p = bokeh.plotting.figure(width=400, height=400)
p.x_range.range_padding = p.y_range.range_padding = 0

# must give a vector of image data for image parameter
p.image(image=[img], x=0, y=0, dw=1024, dh=1024)

bokeh.io.show(p)

In [5]:
threshold_tip = df_general_info["tip_threshold"][idx]

def find_tip(img: np.ndarray, threshold_tip: int = 750) -> list:
    tip_mask = img < threshold_tip
    tip_mask = np.array(tip_mask.astype(int))
    tip_outline = np.array([[0, 0]])
    tip_end = [0, 0]
    for i in range(1, tip_mask.shape[0]-1):
        for j in range(1, 300):
            if np.sum(tip_mask[i, j] != tip_mask[i-1:i+1, j-1:j+1])==2:
                tip_outline = np.concatenate([tip_outline, [[j, i]]], axis=0)
                if j > tip_end[0]:
                    tip_end = [j, i]

    if tip_outline.shape[0] > 20:
        return tip_outline, tip_end

    else:
        print("No tip found... try another threshold.")


img = cv2.imread(tip_file, cv2.IMREAD_UNCHANGED)

tip_outline, tip_end = find_tip(img, threshold_tip)

p = bokeh.plotting.figure(width=400, height=400, title="Yay, we found a tip!!!")
p.x_range.range_padding = p.y_range.range_padding = 0
p.image(image=[img], x=0, y=0, dw=1024, dh=1024)
p.circle(x=tip_outline[:, 0], y=tip_outline[:, 1], color='red')
p.star(x=tip_end[0], y=tip_end[1], color='cyan', size=15)
bokeh.io.show(p)
    

## Distance from tip

In [6]:
def add_distance_from_tip(df: pd.DataFrame, tip_point: list[int, int]) -> None:
    '''
    calculates distance from the tip end point (tip_point) to bead and adds this to the dataframe df
    '''
    df['DISTANCE [um]'] = np.sqrt((df['POSITION_X']-tip_point[0])**2+(df['POSITION_Y']-tip_point[1])**2)


def add_force(df: pd.DataFrame, force_calibration_params: list) -> None:
    a1, k1, a2, k2 = force_calibration_params
    df['FORCE [pN]'] = a1*np.exp(df['DISTANCE [um]']/k1)+a2*np.exp(df['DISTANCE [um]']/k2)


#######
# define force calibration parameters
#######
force_calibration_params = [6.47755226e+02, -5.16372481e+01, 1.87872313e+01, 4.49671461e+08]

add_distance_from_tip(df, tip_end)
add_force(df, force_calibration_params)

df.head()

LABEL       ID  TRACK_ID   QUALITY  POSITION_X  POSITION_Y  \
955  ID1004879  1004879         6  1.260095  454.989749  310.672957   
318  ID1004883  1004883         2  1.355185  396.298637  331.199508   
571  ID1004881  1004881         4  1.854667  414.375458  323.841809   
174  ID1004884  1004884         1  0.948853  441.221933  339.588423   
704  ID1004880  1004880         5  1.158269  424.353404  318.606559   

     POSITION_Z  POSITION_T  FRAME  RADIUS  ...  MEAN_INTENSITY_CH1  \
955         0.0         0.0      0     6.0  ...          434.841155   
318         0.0         0.0      0     6.0  ...          439.768953   
571         0.0         0.0      0     6.0  ...          436.570397   
174         0.0         0.0      0     6.0  ...          430.534296   
704         0.0         0.0      0     6.0  ...          429.812274   

     MEDIAN_INTENSITY_CH1  MIN_INTENSITY_CH1  MAX_INTENSITY_CH1  \
955                 432.0              391.0              499.0   
318                 439.0              394.0              493.0   
571                 419.0              393.0              605.0   
174                 428.0              388.0              482.0   
704                 420.0              390.0              597.0   

     TOTAL_INTENSITY_CH1  STD_INTENSITY_CH1  CONTRAST_CH1   SNR_CH1  \
955             120451.0          19.168306      0.021347  0.948305   
318             121816.0          17.921448      0.028751  1.371607   
571             120930.0          43.179851      0.023556  0.465366   
174             119258.0          14.740377      0.012063  0.696288   
704             119058.0          35.077979      0.009737  0.236312   

     DISTANCE [um]  FORCE [pN]  
955     359.341259   19.402672  
318     299.521369   20.747396  
571     318.453685   20.145745  
174     332.252399   19.827180  
704     329.613407   19.881708  

[5 rows x 22 columns]

### Magnet on, magnet off

In [7]:
print(first_pulse, t_on, t_off)

magnet_on = np.array([first_pulse + j*(t_on+t_off) + i - 1 for i in range(0, t_on) for j in range(20)])
df['MAGNET_STATUS'] = [1 if df['FRAME'].values[i] in magnet_on else 0 for i in range(len(df))]

df

6 6 18


LABEL       ID  TRACK_ID   QUALITY  POSITION_X  POSITION_Y  \
955   ID1004879  1004879         6  1.260095  454.989749  310.672957   
318   ID1004883  1004883         2  1.355185  396.298637  331.199508   
571   ID1004881  1004881         4  1.854667  414.375458  323.841809   
174   ID1004884  1004884         1  0.948853  441.221933  339.588423   
704   ID1004880  1004880         5  1.158269  424.353404  318.606559   
...         ...      ...       ...       ...         ...         ...   
1659  ID1007821  1007821        53  0.779008  420.540686  320.944224   
1329  ID1007822  1007822        52  1.189613  460.906103  352.634537   
1333  ID1007818  1007818        52  1.224907  460.862430  352.868810   
1662  ID1007817  1007817        53  0.792068  420.315932  320.986595   
1990  ID1007816  1007816        54  1.146900  399.092242  310.648332   

      POSITION_Z  POSITION_T  FRAME  RADIUS  ...  MEDIAN_INTENSITY_CH1  \
955          0.0         0.0      0     6.0  ...                 432.0   
318          0.0         0.0      0     6.0  ...                 439.0   
571          0.0         0.0      0     6.0  ...                 419.0   
174          0.0         0.0      0     6.0  ...                 428.0   
704          0.0         0.0      0     6.0  ...                 420.0   
...          ...         ...    ...     ...  ...                   ...   
1659         0.0      2240.0    448     6.0  ...                 410.0   
1329         0.0      2240.0    448     6.0  ...                 413.0   
1333         0.0      2245.0    449     6.0  ...                 414.0   
1662         0.0      2245.0    449     6.0  ...                 411.0   
1990         0.0      2245.0    449     6.0  ...                 411.0   

      MIN_INTENSITY_CH1  MAX_INTENSITY_CH1  TOTAL_INTENSITY_CH1  \
955               391.0              499.0             120451.0   
318               394.0              493.0             121816.0   
571               393.0              605.0             120930.0   
174               388.0              482.0             119258.0   
704               390.0              597.0             119058.0   
...                 ...                ...                  ...   
1659              379.0              474.0             114648.0   
1329              386.0              564.0             116468.0   
1333              386.0              567.0             117154.0   
1662              391.0              468.0             114793.0   
1990              381.0              500.0             116026.0   

      STD_INTENSITY_CH1  CONTRAST_CH1   SNR_CH1  DISTANCE [um]  FORCE [pN]  \
955           19.168306      0.021347  0.948305     359.341259   19.402672   
318           17.921448      0.028751  1.371607     299.521369   20.747396   
571           43.179851      0.023556  0.465366     318.453685   20.145745   
174           14.740377      0.012063  0.696288     332.252399   19.827180   
704           35.077979      0.009737  0.236312     329.613407   19.881708   
...                 ...           ...       ...            ...         ...   
1659          13.771525      0.009601  0.571618     325.152058   19.980472   
1329          29.235603      0.015108  0.428094     343.120417   19.629805   
1333          30.410951      0.017179  0.469758     342.974215   19.632194   
1662          13.641005      0.009309  0.560400     324.944578   19.985277   
1990          22.403582      0.015136  0.557539     314.380224   20.257252   

      MAGNET_STATUS  
955               0  
318               0  
571               0  
174               0  
704               0  
...             ...  
1659              0  
1329              0  
1333              0  
1662              0  
1990              0  

[2169 rows x 23 columns]

## Let's plot distance from tip in time for each bead

In [8]:
df = df[df['FRAME']<250] # this is relevant for this specific file

p = bokeh.plotting.figure(
    frame_width = 400,
    frame_height = 300,
    x_axis_label='frame',
    y_axis_label='distance from tip [um]',
    title=filename
)

source_on = bokeh.models.ColumnDataSource(df[df["MAGNET_STATUS"]==1])
source_off = bokeh.models.ColumnDataSource(df[df["MAGNET_STATUS"]==0])
p.circle(source=source_on, x='FRAME', y='DISTANCE [um]', alpha=0.5, color='green', legend_label='Magnet ON')
p.circle(source=source_off, x='FRAME', y='DISTANCE [um]', alpha=0.5, legend_label='Magnet OFF')

p.legend.click_policy = 'hide'

bokeh.io.show(p)
bokeh.io.save(p, f"distance_from_tip.html")

/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/3935023713.py:19: UserWarning: save() called but no resources were supplied and output_file(...) was never called, defaulting to resources.CDN
  bokeh.io.save(p, f"distance_from_tip.html")
/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/3935023713.py:19: UserWarning: save() called but no title was supplied and output_file(...) was never called, using default title 'Bokeh Plot'
  bokeh.io.save(p, f"distance_from_tip.html")


'/Users/ursic/PhD/Projects/1_Scripts/beads_in_zebrafish/archive/distance_from_tip.html'

## Correcting for background flows

In [9]:
def add_flow_slope(df: pd.DataFrame, first_pulse: int, t_on: int, t_off: int):
    '''
    This function checks out the bead tracks. It takes into account the last 2/3 of the OFF phase before the new period starts. It calculates the slopes where possible and adds them into the data frame. 
    
    ############################################################################
    df:             dataframe with bead tracks
    first_pulse:    frame number at which the first pulse starts
    t_on:           length of the ON phase (in number of frames)
    t_off:          length of the OFF phase (in number of frames)
    plot:           plot or not? this is the question.... 
    ############################################################################

    Returns none, because the point is to add a column into the dataframe. 
    '''

    df['CORRECTION_k'] = np.nan
    df['CORRECTION_k_ERR'] = np.nan
    df['CORRECTION_N'] = np.nan
    df['CORRECTION_N_ERR'] = np.nan

    periods = np.array([[first_pulse + j*(t_on+t_off) + i - 1 for i in range(0, t_on+t_off)] for j in range(-1, 20)])

    for idx in df['TRACK_ID'].unique():
        track = df[df["TRACK_ID"] == idx]

        for period in periods:
            interval = np.array([period[-1] - t_off*2//3 + i for i in range(0, t_off*2//3)])
            xdata = track[track["FRAME"].isin(interval)]["FRAME"].values
            ydata = track[track["FRAME"].isin(interval)]["DISTANCE [um]"].values
            if len(xdata) >= 5:
                f = lambda x, *p: p[0]*x + p[1]
                popt, pcov = curve_fit(f, xdata, ydata, p0=[-1, 300], nan_policy='raise')
                if (pcov[1][1]/popt[1] < 0.3) & (pcov[0][0]/popt[0] < 0.01):
                    df.loc[(df["TRACK_ID"]==idx) & (df["FRAME"].isin(period)), 'CORRECTION_k'] = popt[0]
                    df.loc[(df["TRACK_ID"]==idx) & (df["FRAME"].isin(period)), 'CORRECTION_k_ERR'] = pcov[0][0]
                    df.loc[(df["TRACK_ID"]==idx) & (df["FRAME"].isin(period)), 'CORRECTION_N'] = popt[1]
                    df.loc[(df["TRACK_ID"]==idx) & (df["FRAME"].isin(period)), 'CORRECTION_N_ERR'] = pcov[1][1]


def calculate_displacement(df: pd.DataFrame, first_pulse: int, t_on: int, t_off: int):
    '''This function substracts the signal from the background (so that we get increasing displacement after each first point of the new pulse). It creates a new column in the df dataframe with the displacement values after each pulse. 

    ############################################################################
    df:             dataframe with bead tracks
    first_pulse:    frame number at which the first pulse starts
    t_on:           length of the ON phase (in number of frames)
    t_off:          length of the OFF phase (in number of frames)
    plot:           plot or not? this is the question.... 
    ############################################################################

    Returns none, because the point is to add a column into the dataframe. 
    '''

    add_flow_slope(df, first_pulse, t_on, t_off)

    df['CORRECTED DISPLACEMENT'] = np.nan

    periods = np.array([[first_pulse + j*(t_on+t_off) + i - 1 for i in range(0, t_on+t_off)] for j in range(-1, 20)])


    # background is calculated as accelerated movement
    background_func = lambda t, t_1, x_1, k_1, k_2: x_1 + k_1*(t-t_1) + (k_2-k_1)/(2*(t_on+t_off))*(t-t_1)**2

    for idx in df['TRACK_ID'].unique():
        track = df[df["TRACK_ID"] == idx]

        for (period_1, period_2) in zip(periods[:-1], periods[1:]):
            popt_1 = track.loc[track["FRAME"]==period_1[0],  ["CORRECTION_k", "CORRECTION_N"]].values
            popt_2 = track.loc[track["FRAME"]==period_2[0],  ["CORRECTION_k", "CORRECTION_N"]].values
            
            if (popt_1.shape != (0,2)) & (popt_2.shape != (0,2)):
                if not (np.isnan(popt_1).any() or np.isnan(popt_2).any()):
                    k_1, N_1 = popt_1[0]
                    k_2, _ = popt_2[0]
                    x_1 = k_1*period_2[0] + N_1
                    time = track[track["FRAME"].isin(period_2)]["FRAME"].values
                    data = track[track["FRAME"].isin(period_2)]["DISTANCE [um]"].values
                    if len(time) >= 5:
                        corrected_data = background_func(time, time[0], x_1, k_1, k_2) - data
                        df.loc[(df['TRACK_ID']==idx) & (df["FRAME"].isin(period_2)), 'CORRECTED DISPLACEMENT'] = corrected_data


calculate_displacement(df, first_pulse, t_on, t_off)

df.head(200)


/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/6491498.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['CORRECTION_k'] = np.nan
/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/6491498.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['CORRECTION_k_ERR'] = np.nan
/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/6491498.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,c

/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/6491498.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['CORRECTED DISPLACEMENT'] = np.nan


LABEL       ID  TRACK_ID   QUALITY  POSITION_X  POSITION_Y  \
955  ID1004879  1004879         6  1.260095  454.989749  310.672957   
318  ID1004883  1004883         2  1.355185  396.298637  331.199508   
571  ID1004881  1004881         4  1.854667  414.375458  323.841809   
174  ID1004884  1004884         1  0.948853  441.221933  339.588423   
704  ID1004880  1004880         5  1.158269  424.353404  318.606559   
..         ...      ...       ...       ...         ...         ...   
591  ID1005191  1005191         4  1.858718  398.751008  327.029562   
63   ID1005194  1005194         1  0.784359  429.816646  338.999654   
340  ID1005193  1005193         2  1.153742  379.244507  334.233257   
868  ID1005210  1005210         6  1.415768  431.744892  309.515681   
69   ID1005215  1005215         1  0.814741  428.521555  338.423249   

     POSITION_Z  POSITION_T  FRAME  RADIUS  ...  CONTRAST_CH1   SNR_CH1  \
955         0.0         0.0      0     6.0  ...      0.021347  0.948305   
318         0.0         0.0      0     6.0  ...      0.028751  1.371607   
571         0.0         0.0      0     6.0  ...      0.023556  0.465366   
174         0.0         0.0      0     6.0  ...      0.012063  0.696288   
704         0.0         0.0      0     6.0  ...      0.009737  0.236312   
..          ...         ...    ...     ...  ...           ...       ...   
591         0.0       160.0     32     6.0  ...      0.025720  0.491805   
63          0.0       160.0     32     6.0  ...      0.011775  0.835144   
340         0.0       160.0     32     6.0  ...      0.021649  1.085898   
868         0.0       165.0     33     6.0  ...      0.028253  1.422479   
69          0.0       165.0     33     6.0  ...      0.011460  0.775690   

     DISTANCE [um]  FORCE [pN]  MAGNET_STATUS  CORRECTION_k  CORRECTION_k_ERR  \
955     359.341259   19.402672              0           NaN               NaN   
318     299.521369   20.747396              0           NaN               NaN   
571     318.453685   20.145745              0           NaN               NaN   
174     332.252399   19.827180              0           NaN               NaN   
704     329.613407   19.881708              0           NaN               NaN   
..             ...         ...            ...           ...               ...   
591     303.983936   20.585111              1      0.036296          0.000075   
63      322.826074   20.035450              1           NaN               NaN   
340     284.133873   21.427865              1     -0.054976          0.000512   
868     340.924050   19.666416              1           NaN               NaN   
69      322.035059   20.054718              1           NaN               NaN   

     CORRECTION_N  CORRECTION_N_ERR  CORRECTED DISPLACEMENT  
955           NaN               NaN                     NaN  
318           NaN               NaN                     NaN  
571           NaN               NaN                     NaN  
174           NaN               NaN                     NaN  
704           NaN               NaN                     NaN  
..            ...               ...                     ...  
591    302.848059          0.155523                7.265241  
63            NaN               NaN                     NaN  
340    285.736483          1.066676                7.815106  
868           NaN               NaN                     NaN  
69            NaN               NaN                     NaN  

[200 rows x 28 columns]

In [10]:
p = bokeh.plotting.figure(
frame_width = 400,
frame_height = 300,
x_axis_label='frame',
y_axis_label='distance from tip (um)',
title=filename
)
source_on = bokeh.models.ColumnDataSource(df[df["MAGNET_STATUS"]==1])
source_off = bokeh.models.ColumnDataSource(df[df["MAGNET_STATUS"]==0])
p.circle(source=source_on, x='FRAME', y='DISTANCE [um]', alpha=0.5, color='green', legend_label='Magnet ON')
p.circle(source=source_off, x='FRAME', y='DISTANCE [um]', alpha=0.5, legend_label='Magnet OFF')

for idx in df['TRACK_ID'].unique():
    track = df[df["TRACK_ID"] == idx]
    periods = np.array([[first_pulse + j*(t_on+t_off) + i - 1 for i in range(0, t_on+t_off)] for j in range(-1, 20)])

    for period in periods:
        interval = np.array([period[-1] - t_off*2//3 + i for i in range(0, t_off*2//3)])

        xdata = track[track["FRAME"].isin(interval)]["FRAME"].values
        ydata = track[track["FRAME"].isin(interval)]["DISTANCE [um]"].values
        popt = track.loc[track["FRAME"] == interval[0],  ["CORRECTION_k", "CORRECTION_N"]].values
        if popt.size != 0:
            f = lambda x, k, N: k*x + N  
            p.circle(x=xdata, y=ydata, alpha=0.3, size=2, color='red')
            x_fit = np.linspace(min(xdata), max(xdata), 30)
            y_fit = f(x_fit, *popt[0])
            p.line(x=x_fit, y=y_fit, alpha=0.3, line_width=2, color='black')

p.legend.click_policy = 'hide'
bokeh.io.show(p)

In [11]:
dt = 5/60 #s

p = bokeh.plotting.figure(
        frame_width = 400,
        frame_height = 300,
        x_axis_label='time [min]',
        y_axis_label='displacement [um]',
        title=filename,
        )

colors = cc.b_glasbey_category10

for color, (track, g) in zip(colors, df.groupby('TRACK_ID')):
        time = g['FRAME']*dt
        displacement = g['CORRECTED DISPLACEMENT']
        p.circle(x=time, y=displacement, alpha=0.5, color=color)
        

# p.legend.click_policy = 'hide'

p.output_backend = "svg" 

bokeh.io.show(p)
# bokeh.io.export_svg(p, filename='20230908_s03_tracks_corrected.svg')
# bokeh.io.save(p, filename='20230908_s03_30sON_90sOFF_1000mV_1-tracks_corrected.html')

In [12]:
dt = 5 #s

p = bokeh.plotting.figure(
        frame_width = 400,
        frame_height = 300,
        x_axis_label='time [s]',
        y_axis_label='displacement / force [um/pN]',
        title=filename,
        )

time = df['FRAME']*dt
displacement_force_ratio = df['CORRECTED DISPLACEMENT']/df['FORCE [pN]']

colors = cc.b_glasbey_category10

magnet_pulses = np.array([[first_pulse + j*(t_on+t_off) + i - 1 for i in range(0, t_on)] for j in range(20)])


for color, (track, g) in zip(colors, df.groupby('TRACK_ID')):
        for magnet_pulse in magnet_pulses:
                time = g.loc[g['FRAME'].isin(magnet_pulse), 'FRAME']*dt
                displacement_force_ratio = g.loc[g['FRAME'].isin(magnet_pulse), 'CORRECTED DISPLACEMENT']/g.loc[g['FRAME'].isin(magnet_pulse), 'FORCE [pN]']
                if time.empty or (~displacement_force_ratio.notna()).any():
                        continue
                p.circle(x=time, y=displacement_force_ratio, alpha=0.5, color=color)
                f = lambda x, *p: p[0]*x + p[1]
                popt, pcov = curve_fit(f, time, displacement_force_ratio, p0=[0.1, 10], nan_policy='raise')
                x_fit = np.linspace(min(time), max(time), 30)
                y_fit = f(x_fit, *popt)
                eff_viscosity = 1000/(popt[0]*6*np.pi*1.4) #mPas
                df.loc[(df['FRAME'].isin(magnet_pulse)) & (df['TRACK_ID']==track), 'EFF_VISCOSITY']=eff_viscosity
                p.line(x=x_fit, y=y_fit, alpha=0.3, line_width=2, color='black')


p.circle(x=time[df['MAGNET_STATUS']==1], y=displacement_force_ratio[df['MAGNET_STATUS']==1], alpha=0.5, color='green')


# p.legend.click_policy = 'hide'

p.output_backend = "svg" 

bokeh.io.show(p)

/var/folders/c1/95zwm3_14_j1wp412s49dvlr0000gp/T/ipykernel_45484/471305363.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df.loc[(df['FRAME'].isin(magnet_pulse)) & (df['TRACK_ID']==track), 'EFF_VISCOSITY']=eff_viscosity


## Get results

In [13]:
result_df = pd.DataFrame(columns=['FILENAME', 'TRACK_IDX', 'PULSE_START_TIME', 'MAGNET_STATUS', 'VISCOSITY'])

N_pulses = np.max(df['FRAME'])//(t_on+t_off)

for track_idx in df['TRACK_ID'].unique():    
    for i in range(N_pulses):
        pulse_start = first_pulse + i*(t_on+t_off)
        pulse_frames = np.array([first_pulse + frame - 1 for frame in range(i*(t_on+t_off), (i+1)*(t_on+t_off))])
        df_pulse = df[(df['TRACK_ID']==track_idx)&(df['FRAME'].isin(pulse_frames))]
        viscosity = df_pulse.loc[df_pulse['MAGNET_STATUS']==1, 'EFF_VISCOSITY'].values
        if len(viscosity) > 0:
            new_result_row = {
                'FILENAME' : filename, 
                'TRACK_IDX' : track_idx,
                'PULSE_START_TIME' : pulse_start,
                'MAGNET_STATUS' : 1,
                'VISCOSITY' : viscosity[0]
                }
            df_new_row = pd.DataFrame([new_result_row], columns=result_df.columns) 
            result_df = pd.concat([result_df, df_new_row], ignore_index=True)

result_df = result_df[result_df['VISCOSITY'].notna()&(result_df['VISCOSITY']>0)]
result_df

FILENAME TRACK_IDX PULSE_START_TIME  \
3   20230913_s01_30sON_90sOFF_1000mV_1         6               78   
4   20230913_s01_30sON_90sOFF_1000mV_1         6              102   
9   20230913_s01_30sON_90sOFF_1000mV_1         6              222   
11  20230913_s01_30sON_90sOFF_1000mV_1         2               30   
12  20230913_s01_30sON_90sOFF_1000mV_1         2               54   
13  20230913_s01_30sON_90sOFF_1000mV_1         2               78   
16  20230913_s01_30sON_90sOFF_1000mV_1         4               30   
17  20230913_s01_30sON_90sOFF_1000mV_1         4               54   
18  20230913_s01_30sON_90sOFF_1000mV_1         4               78   
19  20230913_s01_30sON_90sOFF_1000mV_1         4              102   
27  20230913_s01_30sON_90sOFF_1000mV_1         1              174   
28  20230913_s01_30sON_90sOFF_1000mV_1         1              198   
29  20230913_s01_30sON_90sOFF_1000mV_1         1              222   
31  20230913_s01_30sON_90sOFF_1000mV_1         5               30   
32  20230913_s01_30sON_90sOFF_1000mV_1         5               54   
33  20230913_s01_30sON_90sOFF_1000mV_1         5               78   
48  20230913_s01_30sON_90sOFF_1000mV_1        52              150   
49  20230913_s01_30sON_90sOFF_1000mV_1        52              174   
50  20230913_s01_30sON_90sOFF_1000mV_1        52              198   
54  20230913_s01_30sON_90sOFF_1000mV_1        54              174   
55  20230913_s01_30sON_90sOFF_1000mV_1        54              198   
58  20230913_s01_30sON_90sOFF_1000mV_1        53              150   
59  20230913_s01_30sON_90sOFF_1000mV_1        53              174   

   MAGNET_STATUS     VISCOSITY  
3              1   5688.291265  
4              1  11246.629794  
9              1   8919.156816  
11             1   4339.830050  
12             1   4517.603539  
13             1   3760.782722  
16             1   5230.986488  
17             1   6168.051639  
18             1   5009.723570  
19             1   6266.020502  
27             1   3980.433319  
28             1  24105.216898  
29             1  10226.199887  
31             1   4831.757858  
32             1   5248.464676  
33             1   4458.524937  
48             1  10557.739758  
49             1  15821.610903  
50             1   7835.636981  
54             1  22027.624143  
55             1   4266.009989  
58             1   7966.703968  
59             1   7629.153906

In [14]:
p = iqplot.stripbox(result_df, spread ='jitter', q='VISCOSITY')
bokeh.io.show(p)